In [44]:
%matplotlib inline
import string
import re
import pandas as pd
import numpy as np
import matplotlib
import matplotlib.pyplot as plt
import plotly as py
import psycopg2
import textblob
import textatistic
import os
import math
import random
from nltk.corpus import stopwords
import seaborn as sbn
import requests
from wordcloud import *
from bs4 import BeautifulSoup
from collections import Counter
matplotlib.style.use('ggplot')
py.offline.init_notebook_mode()

In [21]:
opp = pd.read_csv('/home/faculty/millbr02/pub/ecomm/order_products__prior.csv')

In [22]:
opt = pd.read_csv('/home/faculty/millbr02/pub/ecomm/order_products__train.csv')

In [23]:
order = pd.read_csv('/home/faculty/millbr02/pub/ecomm/orders.csv')

In [24]:
products = pd.read_csv('/home/faculty/millbr02/pub/ecomm/products.csv')

In [25]:
aisles = pd.read_csv('/home/faculty/millbr02/pub/ecomm/aisles.csv')

In [26]:
departments = pd.read_csv('/home/faculty/millbr02/pub/ecomm/departments.csv')

In [27]:
opp.head()

order_id  product_id  add_to_cart_order  reordered
0         2       33120                  1          1
1         2       28985                  2          1
2         2        9327                  3          0
3         2       45918                  4          1
4         2       30035                  5          0

In [28]:
opt.head()

order_id  product_id  add_to_cart_order  reordered
0         1       49302                  1          1
1         1       11109                  2          1
2         1       10246                  3          0
3         1       49683                  4          0
4         1       43633                  5          1

In [29]:
aisles.head()

aisle_id                       aisle
0         1       prepared soups salads
1         2           specialty cheeses
2         3         energy granola bars
3         4               instant foods
4         5  marinades meat preparation

In [30]:
departments.head()

department_id department
0              1     frozen
1              2      other
2              3     bakery
3              4    produce
4              5    alcohol

In [31]:
order.head()

order_id  user_id eval_set  order_number  order_dow  order_hour_of_day  \
0   2539329        1    prior             1          2                  8   
1   2398795        1    prior             2          3                  7   
2    473747        1    prior             3          3                 12   
3   2254736        1    prior             4          4                  7   
4    431534        1    prior             5          4                 15   

   days_since_prior_order  
0                     NaN  
1                    15.0  
2                    21.0  
3                    29.0  
4                    28.0

In [32]:
products.head()

product_id                                       product_name  aisle_id  \
0           1                         Chocolate Sandwich Cookies        61   
1           2                                   All-Seasons Salt       104   
2           3               Robust Golden Unsweetened Oolong Tea        94   
3           4  Smart Ones Classic Favorites Mini Rigatoni Wit...        38   
4           5                          Green Chile Anytime Sauce         5   

   department_id  
0             19  
1             13  
2              7  
3              1  
4             13

In [52]:
order_product = opt.merge(products, how= 'inner',on = 'product_id')

In [53]:
order_product = order_product.merge(order, how= 'inner',on = 'order_id')

In [35]:
order_product.head()

order_id  product_id  add_to_cart_order  reordered  \
0         1       49302                  1          1   
1         1       11109                  2          1   
2         1       10246                  3          0   
3         1       49683                  4          0   
4         1       43633                  5          1   

                                    product_name  aisle_id  department_id  \
0                               Bulgarian Yogurt       120             16   
1  Organic 4% Milk Fat Whole Milk Cottage Cheese       108             16   
2                          Organic Celery Hearts        83              4   
3                                 Cucumber Kirby        83              4   
4           Lightly Smoked Sardines in Olive Oil        95             15   

   user_id eval_set  order_number  order_dow  order_hour_of_day  \
0   112108    train             4          4                 10   
1   112108    train             4          4                 10   
2   112108    train             4          4                 10   
3   112108    train             4          4                 10   
4   112108    train             4          4                 10   

   days_since_prior_order  
0                     9.0  
1                     9.0  
2                     9.0  
3                     9.0  
4                     9.0

In [36]:
a = order_product.groupby(['product_name'])['product_id'].count()

amount of food at checkout?

What is the most popular food item?

In [37]:
a.sort_values(ascending = False)

product_name
Banana                                                                                18726
Bag of Organic Bananas                                                                15480
Organic Strawberries                                                                  10894
Organic Baby Spinach                                                                   9784
Large Lemon                                                                            8135
Organic Avocado                                                                        7409
Organic Hass Avocado                                                                   7293
Strawberries                                                                           6494
Limes                                                                                  6033
Organic Raspberries                                                                    5546
Organic Blueberries                                                

In [157]:
aco = order_product.groupby('order_id')['add_to_cart_order'].max()
aco = pd.DataFrame(aco)
aco = aco.reset_index()

In [42]:
#fig, axes = plt.subplots(nrows=1 , ncols=1 , figsize(10,10))
#axes.violinplot(aco['add_to_cart_order'],showmeans=True,showmedians=False)

SyntaxError: positional argument follows keyword argument (<ipython-input-42-a905cef73a8c>, line 1)

In [61]:
pivot = pd.pivot_table(order_product[order_product.order_id<60],values='add_to_cart_order', index=['order_id'], columns=['product_id'])

In [62]:
pivot

product_id  4461   10246  11109  11913  13176  18159  19660  21616  22035  \
order_id                                                                    
1             NaN    3.0    2.0    NaN    6.0    NaN    NaN    NaN    8.0   
36            NaN    NaN    NaN    NaN    NaN    NaN    2.0    NaN    NaN   
38            3.0    NaN    NaN    1.0    NaN    2.0    NaN    4.0    NaN   

product_id  23622  ...    42625  43086  43633  46620  46979  47209  48679  \
order_id           ...                                                      
1             NaN  ...      NaN    NaN    5.0    NaN    NaN    7.0    NaN   
36            NaN  ...      NaN    4.0    NaN    5.0    8.0    NaN    7.0   
38            5.0  ...      8.0    NaN    NaN    NaN    NaN    NaN    NaN   

product_id  49235  49302  49683  
order_id                         
1             NaN    1.0    4.0  
36            3.0    NaN    NaN  
38            NaN    NaN    NaN  

[3 rows x 25 columns]

In [63]:
pivot.iloc[1][pivot.iloc[1].notnull()]

product_id
19660    2.0
34497    6.0
39612    1.0
43086    4.0
46620    5.0
46979    8.0
48679    7.0
49235    3.0
Name: 36, dtype: float64

In [67]:
order_product.sort_values('order_id').head(20)

order_id  product_id  add_to_cart_order  reordered  \
0              1       49302                  1          1   
1              1       11109                  2          1   
2              1       10246                  3          0   
3              1       49683                  4          0   
4              1       43633                  5          1   
5              1       13176                  6          0   
6              1       47209                  7          0   
7              1       22035                  8          1   
366950        36       46979                  8          1   
366948        36       34497                  6          1   
366947        36       46620                  5          1   
366949        36       48679                  7          1   
366945        36       49235                  3          0   
366944        36       19660                  2          1   
366943        36       39612                  1          0   
366946        36       43086                  4          1   
473772        38       39693                  9          0   
473771        38       42625                  8          0   
473770        38       28842                  7          0   
473769        38       32433                  6          0   

                                         product_name  aisle_id  \
0                                    Bulgarian Yogurt       120   
1       Organic 4% Milk Fat Whole Milk Cottage Cheese       108   
2                               Organic Celery Hearts        83   
3                                      Cucumber Kirby        83   
4                Lightly Smoked Sardines in Olive Oil        95   
5                              Bag of Organic Bananas        24   
6                                Organic Hass Avocado        24   
7                         Organic Whole String Cheese        21   
366950                                      Asparagus        83   
366948                          Prosciutto, Americano        96   
366947            Cage Free Extra Large Grade AA Eggs        86   
366949              Organic Garnet Sweet Potato (Yam)        83   
366945                            Organic Half & Half        53   
366944                                   Spring Water       115   
366943                  Grated Pecorino Romano Cheese         2   
366946                             Super Greens Salad       123   
473772                                     Fresh Dill        16   
473771                            Flat Parsley, Bunch        16   
473770                               Bunched Cilantro        16   
473769                                     Green Peas       116   

        department_id  user_id eval_set  order_number  order_dow  \
0                  16   112108    train             4          4   
1                  16   112108    train             4          4   
2                   4   112108    train             4          4   
3                   4   112108    train             4          4   
4                  15   112108    train             4          4   
5                   4   112108    train             4          4   
6                   4   112108    train             4          4   
7                  16   112108    train             4          4   
366950              4    79431    train            23          6   
366948             20    79431    train            23          6   
366947             16    79431    train            23          6   
366949              4    79431    train            23          6   
366945             16    79431    train            23          6   
366944              7    79431    train            23          6   
366943             16    79431    train            23          6   
366946              4    79431    train            23          6   
473772              4    42756    train             6          6   
473771              4    42756    train             6          6   
47377

In [86]:
current_order = 1
item = []
for i in order_product['order_id']:
    for j in order_product['product_id']:
        if i == current_order:
            item.append(j)


KeyboardInterrupt: 

In [145]:
ms = {}

In [146]:
for a in order_product['product_id']:
    ms[a] = {}

In [147]:
ms

{1: {},
 2: {},
 3: {},
 4: {},
 5: {},
 7: {},
 8: {},
 9: {},
 10: {},
 11: {},
 12: {},
 13: {},
 14: {},
 15: {},
 16: {},
 18: {},
 21: {},
 22: {},
 23: {},
 25: {},
 26: {},
 27: {},
 28: {},
 29: {},
 30: {},
 31: {},
 32: {},
 33: {},
 34: {},
 35: {},
 36: {},
 37: {},
 38: {},
 40: {},
 41: {},
 42: {},
 43: {},
 44: {},
 45: {},
 46: {},
 47: {},
 48: {},
 49: {},
 50: {},
 52: {},
 53: {},
 54: {},
 55: {},
 57: {},
 58: {},
 59: {},
 60: {},
 61: {},
 62: {},
 63: {},
 64: {},
 65: {},
 66: {},
 67: {},
 68: {},
 70: {},
 71: {},
 72: {},
 73: {},
 74: {},
 75: {},
 77: {},
 78: {},
 79: {},
 81: {},
 82: {},
 83: {},
 84: {},
 86: {},
 87: {},
 89: {},
 91: {},
 92: {},
 93: {},
 94: {},
 95: {},
 96: {},
 97: {},
 98: {},
 99: {},
 100: {},
 101: {},
 102: {},
 104: {},
 105: {},
 106: {},
 107: {},
 108: {},
 109: {},
 110: {},
 112: {},
 113: {},
 114: {},
 115: {},
 116: {},
 117: {},
 118: {},
 119: {},
 120: {},
 121: {},
 122: {},
 123: {},
 124: {},
 126: {},
 12

In [148]:
len(ms)

39123

In [149]:
len(order_product.product_id.unique())

39123

In [175]:
ol = []
aco.head()


order_id  product_id  add_to_cart_order  reordered  \
0               1       49302                  1          1   
1               1       11109                  2          1   
2               1       10246                  3          0   
3               1       49683                  4          0   
4               1       43633                  5          1   
8          816049       49302                  7          1   
9          816049       22035                 14          0   
10         816049       20574                  2          1   
11         816049       41220                  4          0   
12         816049       34969                  1          1   
24        1242203       49302                  1          1   
25        1242203       16797                  6          1   
26        1242203       47626                  3          1   
27        1242203       21903                  2          1   
28        1242203        5450                  7          1   
34        1383349       49302                 11          1   
35        1383349       13176                  1          1   
36        1383349       48679                 17          0   
37        1383349       46979                 12          1   
38        1383349       21616                  9          0   
57        1787378       49302                  8          0   
58        1787378       22935                  5          1   
59        1787378       33000                  2          1   
60        1787378       21903                  4          1   
61        1787378        5769                  6          0   
65        2445303       49302                  2          1   
66        2445303       13176                  1          1   
67        2445303       35951                  6          1   
68        2445303       27521                  8          1   
69        2445303       27156                 14          1   
...           ...         ...                ...        ...   
1384587   2486383       38649                  1          0   
1384588   2500552       26304                  1          1   
1384589   2550887       39084                  1          0   
1384590   2582697       44850                  1          1   
1384591   2796129       36503                  1          0   
1384592   2666114       31664                  1          0   
1384593   2676219       32154                  1          0   
1384594   2802509       42355                  1          1   
1384595   2751404        6731                  1          0   
1384596   2755627       27300                  1          1   
1384597   2764641       20456                  1          1   
1384598   2779850       19830                  1          0   
1384599   2816325       23900                  1          0   
1384600   2833061       25036                  1          0   
1384601   2839453       28717                  1          0   
1384602   3290664       49166                  1          1   
1384603   2981082       47207                  1          1   
1384604   3065151       47057                  1          1   
1384605   3188385       14920                  1          1   
1384606   3140363       35592                  1          1   
1384607   3189476        9589                  1          0   
1384608   3204691       30397                  1          0   
1384609   3208468       41132                  1          0   
1384610   3230409       14909                  1          1   
1384611   3358267       20421                  2          0   
1384612   3358267       34088                  1          0   
1384613   3302779       13315                  1          0   
1384614   3339757       24892                  1          1   
1384615   3373549       26328                  1          0   
1384616   3381085       24862                  1          1   

                                              product_name  aisle_id  \
0                             

In [154]:
for x in order_product['product_id']:
    ms[a][x] = 0

In [155]:
ms

{1: {},
 2: {},
 3: {},
 4: {},
 5: {},
 7: {},
 8: {},
 9: {},
 10: {},
 11: {},
 12: {},
 13: {},
 14: {},
 15: {},
 16: {},
 18: {},
 21: {},
 22: {},
 23: {},
 25: {},
 26: {},
 27: {},
 28: {},
 29: {},
 30: {},
 31: {},
 32: {},
 33: {},
 34: {},
 35: {},
 36: {},
 37: {},
 38: {},
 40: {},
 41: {},
 42: {},
 43: {},
 44: {},
 45: {},
 46: {},
 47: {},
 48: {},
 49: {},
 50: {},
 52: {},
 53: {},
 54: {},
 55: {},
 57: {},
 58: {},
 59: {},
 60: {},
 61: {},
 62: {},
 63: {},
 64: {},
 65: {},
 66: {},
 67: {},
 68: {},
 70: {},
 71: {},
 72: {},
 73: {},
 74: {},
 75: {},
 77: {},
 78: {},
 79: {},
 81: {},
 82: {},
 83: {},
 84: {},
 86: {},
 87: {},
 89: {},
 91: {},
 92: {},
 93: {},
 94: {},
 95: {},
 96: {},
 97: {},
 98: {},
 99: {},
 100: {},
 101: {},
 102: {},
 104: {},
 105: {},
 106: {},
 107: {},
 108: {},
 109: {},
 110: {},
 112: {},
 113: {},
 114: {},
 115: {},
 116: {},
 117: {},
 118: {},
 119: {},
 120: {},
 121: {},
 122: {},
 123: {},
 124: {},
 126: {},
 12

In [161]:
aco = order_product.groupby('order_id')

In [177]:
unique_orderids = aco.groups.keys()

In [179]:
for oid in unique_orderids:
    print(oid)

1572864
1
2359297
3407881
262154
262157
1310734
1310735
262161
1048594
1310739
2315609
2883611
2359324
2621470
2097183
1048608
2359329
2621474
36
1572901
38
2621480
2359338
786475
2359340
524333
490186
2621487
262192
393224
305843
2883636
2662359
786491
262204
2621450
786495
524352
786498
2097219
2097220
2359367
2097228
1048655
2097232
2621523
1310805
2359384
235687
96
98
1048675
262244
696922
2577767
2060057
112
1572883
1048693
2359414
1048702
1835137
2359432
524430
262287
2621599
1573024
3177351
524452
3189446
3408039
170
1398130
2359470
1310895
1310896
3145905
262322
2621619
1310901
3408056
2097339
1878730
1573055
1835200
262339
2577782
524488
1573066
786635
2097356
262358
218
2009807
2359516
262365
1573086
1048799
2883809
226
3145957
104756
2359528
524524
262382
3408111
2359536
262385
2097394
524532
786678
1048823
1573112
2097401
262395
3408124
2883626
2359551
2097408
262403
262404
1573128
3146000
2097425
1573139
1048854
262425
1311003
2359582
2359583
2883632
2621732
1048870
262439

2101195
1052623
266193
393891
1314772
2625493
3149784
2363354
1879375
1839069
266206
528351
1839072
3411938
4067
2887653
3411943
1052648
1052649
2887658
656039
2101231
2625520
2272595
3411957
1576950
656041
2101240
4090
2887675
4092
2363390
2887679
3411968
743424
528386
787115
2887684
266249
2363403
1576972
2054146
4111
480234
2887698
1052691
2363414
918191
1355098
2749785
1576991
3149859
266279
1577001
1052714
1577003
266285
3149871
1052720
3412017
4146
262835
4148
1577013
1314870
2887736
2887738
1052731
1136650
790590
790593
4164
3149893
2363462
846739
3412041
1314890
3412046
1314895
1577043
528469
1577046
1314903
4185
3149915
3412060
4189
528478
1314912
481296
4194
2625635
1052772
2796902
4201
2363498
4203
1839212
681005
1577070
1839215
2887793
1839218
1577076
3412086
4217
2447381
1615013
1577094
790663
3412104
528521
4234
528529
2625685
2363542
4250
790683
528541
790686
1839263
1562070
1052833
790692
1052838
2887848
4267
1052844
4269
2147486
1052847
2625715
528565
2625718
2625719
5

2627613
530462
481627
6180
268325
2103334
3414056
1316906
6187
654884
1283375
1579058
2889780
6199
1841208
530489
2103354
1841212
1841215
3414081
1836043
2636377
3414087
1579082
1579084
1054797
530511
2103378
1311758
2365527
1841240
2627675
1316956
3414109
268382
792671
1579104
1841249
175803
1841252
2889832
1579115
2098194
2889838
1316976
1841267
1579124
1316981
219497
3151994
3414139
1054848
268418
1399147
530565
1841286
2365575
6282
6286
2365583
2889872
2103441
792722
1579155
2627733
792728
792731
530588
792733
2103454
530591
1317025
2103458
268452
1054885
1579174
792744
792745
2889898
6315
612722
2360349
2365617
3414195
750908
1054904
2103481
87501
6333
2889922
1317060
1268086
3414214
2103496
1317066
530635
6349
268498
6355
6357
1054935
268504
792793
1841370
2627804
2365662
6369
792802
1501607
1317095
1054953
2627818
2889965
2365678
1317103
2627826
268533
268534
2889975
6394
3414267
1579260
2365694
831189
3152128
268548
175830
2627847
1054984
132140
1317131
1054992
1268099
1817417


1319295
1057153
2892163
1581446
1319303
2007965
270730
3416459
1763552
2367886
532879
2105746
8595
1843605
2367895
2892184
1057177
1057179
795036
2892190
2142277
3416480
88816
1581476
2630053
270758
1530609
8616
270762
8619
2841330
270766
1319345
2892211
787870
1792756
2630077
270782
2630082
2367939
795077
2105798
795079
1057224
2105801
1137399
1057228
1581518
2666573
270800
3154385
3173916
132515
1617998
1057242
270812
1319390
270816
2840553
270820
2630117
307281
2105833
2892268
532973
1283458
1843701
1057270
918953
1581560
795129
2892283
1843708
795133
532990
8704
795137
2368002
2630147
270853
532999
1319437
192329
533007
795152
8721
270867
795157
1057303
533016
1836463
2368028
2368029
795169
1843746
2105891
795172
8742
2368043
220331
3154484
2892346
1749087
1057340
2368062
533057
3416642
2368067
8772
1355873
533064
533065
533066
569442
795216
795217
270930
2105941
1319510
1581655
3154520
1581658
1319517
1880165
2368097
3416674
1057379
2892388
785667
2105964
270959
3154546
1843827
22

535397
2108263
11114
1321835
535405
273262
11119
2894705
2055315
1236098
3419000
1321849
3156861
1059711
3156864
535426
1059715
797574
2894727
1846154
613527
2108300
788290
438765
273297
535443
1705796
2894746
535453
11168
797601
1846180
2108325
2894758
797609
1059761
2108339
797628
2370497
1059779
2894788
2894790
2108361
273355
11213
1846222
2632658
2632659
1833472
87664
2894811
1321948
273374
535523
11236
797669
2894822
11239
3156968
3419113
395090
3156974
1059823
2108400
2894833
3419122
3156979
1846261
1584118
1059832
2632697
1846266
569855
273404
273406
1059839
797699
797704
535561
2108427
2632717
797710
3419151
2370576
11282
1094147
3419156
3419158
1846297
2055343
273436
782192
2108451
11301
3419174
797735
1322025
2929159
1846316
273458
2632757
307721
3157048
2632761
1059898
2066689
2370622
2108483
3419208
1846345
1584202
2894924
1322061
3147619
2632788
2632790
535639
3419225
2894938
535643
2108509
1059936
1322082
1924283
2108518
797805
2632814
535664
2361192
3157109
11382
3256311

...

1819957
3130680
1557817
2606396
2459992
2868546
2575243
2093110
2082121
1819979
3392845
1033551
2082128
521784
3130707
2082132
2426173
2606424
1295707
1557852
2344286
1227195
2837392
2344290
1033575
2868584
2531559
509292
1295725
2750013
3392886
2399987
2082170
1557883
3392894
3392896
1295745
2868611
3130756
247174
1295753
1295756
1033614
3392922
3130784
2344353
2606501
1033639
509352
347036
509354
771500
2661860
1033646
497058
3392945
509362
2082228
247223
1557944
636723
3392954
247227
521802
247231
3256605
2082243
2269430
2606534
247239
2246741
1820106
2082251
3130834
2606547
1295829
2868695
2868696
2344410
771547
478249
701711
3130847
3130851
3130853
1820138
1820140
2606574
1033713
2792798
2606582
3130871
1963604
509434
3130875
2740424
1820157
1033727
2868738
2706347
1815146
247304
3072128
247308
1220866
2082318
509455
771604
619268
2868760
2606618
2295244
1820189
2868768
2444208
1558050
1033763
3393060
247333
3130919
1033773
1033774
1033775
2344498
2575283
2344501
1295926
771639
33

2557225
2706901
2872065
2347779
2286625
2085640
1037066
3396366
525408
512784
1299217
1823508
2609944
2138232
3396378
1483567
3134236
3134241
2609959
2609962
2347819
2347821
1948467
2872114
434995
2347828
3231198
2609974
2619529
469953
1823545
512827
774977
2117575
2461497
250694
512839
2609992
3396425
2085713
1789411
2085716
1299285
250712
1046671
2522312
1299297
1561442
104368
2610020
2085733
1037158
775016
3396457
2575847
3037326
1561458
2085748
172862
1561463
1029647
1037177
2872186
2575850
1299327
2872192
3134337
3134340
1037189
1037190
2921750
2750615
3396494
512911
512912
2095256
2872210
3396499
250772
2347925
1299350
378762
1037210
1841449
775070
250784
2347937
2610084
2085797
1823655
653468
1561514
775083
775087
2347954
3134387
915614
2347960
1037241
1823676
2794314
1561535
2610113
892436
2270027
2085828
2872262
3274913
2610120
3134411
3396556
2347981
2775458
775120
1134072
3134419
478713
1823704
775132
775134
522405
1823713
1754161
512998
2592149
2872298
391335
513004
1561581

1826989
2613422
3137711
2089136
3137713
3188083
427456
254133
1661945
2613434
2613435
2875580
2613438
1827007
2613440
2351297
2875586
778440
3137737
1040586
3399883
254156
778446
516305
2613461
516310
778455
1003556
3072549
2875612
2875613
3100709
3137761
2351330
778467
2875622
3144401
2613480
1827049
1536046
2351340
3399917
3057021
2351344
1564913
2351346
2875635
2875637
1827062
3399927
3137784
778491
2089212
1564925
1564926
516351
828800
2351362
1833686
1003564
3013335
254225
2270595
3137812
2089238
1302807
1827099
3013338
2351390
3316772
916187
2613542
1040679
2089260
1396786
2875694
3399984
1827121
2094707
916190
2613558
1040695
516411
3319178
3231797
3137856
260832
254274
959883
2810489
2875720
2613578
1040716
2089293
2351439
3400017
2875731
994849
2705741
516440
3114449
2089309
3400031
1090960
3400034
1565027
1302884
1565029
2875751
1309415
2663826
2875759
2437080
3150923
1827189
254328
3316775
2613626
1040763
1309418
1827199
3400064
610368
254342
2976343
3400075
1827213
516494
1

2092592
2354738
3403315
2092596
2092601
3141178
2879035
1044030
2879040
86624
1178891
479841
2264268
2828058
257611
2616908
86626
1306191
2879059
1047822
3184303
2732039
2616921
2092635
1830492
2092641
2354786
2664379
1308643
1568358
1306215
781929
3141229
3188669
1306224
1830513
3271966
2358547
1044084
257653
1266281
2932808
2842500
1830522
2662310
1830525
781953
1352852
1306243
970633
1044101
1044103
1568394
257676
3141262
3403408
811652
781971
2052718
2461441
3403421
781982
2402245
1306273
2354850
1951771
2092710
3141287
2879145
1044138
1306283
2271176
1528435
2617017
2461442
2879163
3124970
257726
2854249
2879172
1266294
519878
1044167
2879176
3141325
1353677
1047843
2879188
1484750
2183801
2879192
2533327
640678
2617054
671990
1306339
1397372
2751783
1044206
610941
1568498
1353683
2092788
3403509
2354934
2879224
782074
1044219
3141372
2096426
519937
654635
2354950
3403529
3403534
3403535
3141399
348804
2617114
3403548
235540
3141407
3394172
1703216
1044258
3319771
3403556
3232390


1309622
3070849
3144632
43508
3208767
2490186
288022
1571780
742561
261064
2882505
2358218
492803
523214
2621261
1309649
261075
3369374
785367
785368
2970788
2882522
2906735
523228
3058170
2882528
655184
261091
3406821
393041
3406825
1571819
1833964
2096110
3406834
3276627
2358262
1135785
1047550
523263
2882563
1309700
2882565
3364012
2358282
2994027
1833998
742573
3144722
2358291
1834004
1834005
2358294
305668
925245
785438
785440
1834018
2819447
1047589
261158
418961
2882601
1047594
2620459
2533896
742579
3406900
786270
3144759
523321
3144762
1571899
2358337
1834050
1571907
3144773
3406919
3406922
2096205
3144784
1047637
2882649
1047642
1834076
2708666
228693
1571937
3144803
1834086
2882664
1834089
1571947
719262
349131
2278249
1834096
2358385
942724
1047669
2096248
1834105
1571962
1309819
261245
445151
1223189
3406980
3194799
3395567
261256
261257
1571979
1047692
1571982
2358416
1083860
1571988
2358422
1571993
1309850
3037677
3144865
837959
2620580
2437480
1834151
2882728
3360652
10

In [183]:
aco.get_group(1)['product_id']

0    49302
1    11109
2    10246
3    49683
4    43633
5    13176
6    47209
7    22035
Name: product_id, dtype: int64